In [1]:
# Python imports
import os
import glob
import numpy as np
import pandas as pd
import geopandas as gpd
import tarfile
from oggm import utils

In [2]:
rgi_reg_df = []
for rgi_reg in range(1, 20):
    rgi_reg = f'{rgi_reg:02d}'
    rgi_reg_df.append(gpd.read_file(utils.get_rgi_region_file(rgi_reg, version='62')))
rgi_reg_df = pd.concat(rgi_reg_df)

In [3]:
rgi_reg_df = rgi_reg_df.loc[rgi_reg_df.Connect != 2].copy()

In [4]:
df_stats = []
for rgi_reg in range(1, 20):
    rgi_reg = f'{rgi_reg:02d}'
    tmp = pd.read_csv(f'RGI62/b_010/L1/hypsometry/hypsometry_{rgi_reg}_COPDEM30.csv', index_col=0)
    df_stats.append(tmp)
df_stats = pd.concat(df_stats)

In [5]:
assert len(df_stats) == len(rgi_reg_df)

In [6]:
rgi_reg_df = rgi_reg_df.set_index('RGIId')

In [7]:
rgi_reg_df.loc[~rgi_reg_df.index.isin(df_stats.index)]

Empty GeoDataFrame
Columns: [GLIMSId, BgnDate, EndDate, CenLon, CenLat, O1Region, O2Region, Area, Zmin, Zmax, Zmed, Slope, Aspect, Lmax, Status, Connect, Form, TermType, Surging, Linkages, Name, check_geom, geometry]
Index: []

[0 rows x 23 columns]

In [8]:
assert len(df_stats.dropna(how='all')) == len(rgi_reg_df)

In [9]:
rgi_reg_df_all = rgi_reg_df.copy()

In [10]:
rgi_reg_df_all['O1Region'] = rgi_reg_df_all['O1Region'].astype(int)

In [11]:
odir = 'RGI62/b_010/L1/hypsometry_best_dem/'
utils.mkdir(odir)

chosen_dem = []

for rgi_reg in range(1, 20):
    rgi_reg = f'{rgi_reg:02d}'
    min_range = 5
    
    # Ref - RGI
    rgi_reg_df = rgi_reg_df_all.loc[rgi_reg_df_all['O1Region'] == int(rgi_reg)]
    
    # Take COPDEM30 for a start
    source = 'COPDEM30'
    hdf = pd.read_csv(f'RGI62/b_010/L1/hypsometry/hypsometry_{rgi_reg}_{source}.csv', index_col=0)

    ids = np.where(hdf.columns.values == 'dem_source')[0][0]
    attr_cols = list(hdf.columns[0:ids+1])
    hypso_cols = list(hdf.columns[ids+1:])

    hdf_stats = hdf[attr_cols].copy()
    hdf_hypso = hdf[hypso_cols]
    
    valid = (hdf_stats.grid_dx <= 60) & (hdf_stats.valid_dem_perc > 0.99)
    valid = valid & (hdf_stats.zmin_m > -99) & ((hdf_stats.zmax_m - hdf_stats.zmin_m) > min_range)
    output_stats = hdf_stats.loc[valid].copy()
    output_hypso = hdf_hypso.loc[valid].copy()
    
    # Continue with COPDEM90
    source = 'COPDEM90'
    hdf = pd.read_csv(f'RGI62/b_010/L1/hypsometry/hypsometry_{rgi_reg}_{source}.csv', index_col=0)

    ids = np.where(hdf.columns.values == 'dem_source')[0][0]
    attr_cols = list(hdf.columns[0:ids+1])
    hypso_cols = list(hdf.columns[ids+1:])

    hdf_stats = hdf[attr_cols].copy()
    hdf_hypso = hdf[hypso_cols]
    
    valid = (~ hdf_stats.index.isin(output_stats.index)) & (hdf_stats.valid_dem_perc > 0.99) 
    valid = valid & (hdf_stats.zmin_m > -99) & ((hdf_stats.zmax_m - hdf_stats.zmin_m) > min_range)
    output_stats = pd.concat([output_stats, hdf_stats.loc[valid].copy()]).sort_index()
    output_hypso = pd.concat([output_hypso, hdf_hypso.loc[valid].copy()]).sort_index()
    
    still_no_good = rgi_reg_df.loc[~ rgi_reg_df.index.isin(output_stats.index)]
    print(f'{rgi_reg}: After COPDEM, {len(still_no_good)} left bad.')
    if len(still_no_good) == 0:
        print(f'{rgi_reg}:    DONE.')
        pd.concat([output_stats, output_hypso], axis=1).to_csv(odir + f'/hypsometry_{rgi_reg}_best.csv')
        chosen_dem.append(output_stats['dem_source'])
        assert len(output_stats['dem_source']) == len(rgi_reg_df_all.loc[rgi_reg_df_all['O1Region'] == int(rgi_reg)])
        continue
    
    for rang in [min_range, 1]:
        for source in ['NASADEM', 'RAMP', 'DEM3', 'ASTER', 'TANDEM', 'AW3D30', 'MAPZEN']:
            
            hdf = pd.read_csv(f'RGI62/b_010/L1/hypsometry/hypsometry_{rgi_reg}_{source}.csv', index_col=0)
            if 'valid_dem_perc' not in hdf:
                continue

            ids = np.where(hdf.columns.values == 'dem_source')[0][0]
            attr_cols = list(hdf.columns[0:ids+1])
            hypso_cols = list(hdf.columns[ids+1:])

            hdf = hdf.loc[still_no_good.index]

            ids = np.where(hdf.columns.values == 'dem_source')[0][0]
            attr_cols = list(hdf.columns[0:ids+1])
            hypso_cols = list(hdf.columns[ids+1:])

            hdf_stats = hdf[attr_cols].copy()
            hdf_hypso = hdf[hypso_cols]

            valid = (~ hdf_stats.index.isin(output_stats.index)) & (hdf_stats.valid_dem_perc > 0.99) 
            valid = valid & (hdf_stats.zmin_m > -99) & ((hdf_stats.zmax_m - hdf_stats.zmin_m) > rang)
            if len(hdf_stats.loc[valid].copy()) == 0:
                continue
            print(f'{rgi_reg}: {source} and minrange {rang} can take over for {len(hdf_stats.loc[valid].copy())}')
            output_stats = pd.concat([output_stats, hdf_stats.loc[valid].copy()]).sort_index()
            output_hypso = pd.concat([output_hypso, hdf_hypso.loc[valid].copy()]).sort_index()
            still_no_good = rgi_reg_df.loc[~ rgi_reg_df.index.isin(output_stats.index)]

            print(f'{rgi_reg}: After {source} and minrange {rang}, {len(still_no_good)} left bad.')
            if len(still_no_good) == 0:
                print(f'{rgi_reg}:    DONE.')
                pd.concat([output_stats, output_hypso], axis=1).to_csv(odir + f'/hypsometry_{rgi_reg}_best.csv')
                chosen_dem.append(output_stats['dem_source'])
                assert len(output_stats['dem_source']) == len(rgi_reg_df_all.loc[rgi_reg_df_all['O1Region'] == int(rgi_reg)])
                break
           
    if len(still_no_good) > 0:
        out_df = pd.concat([output_stats, output_hypso], axis=1)
        to_complete = hdf_stats.loc[still_no_good.index].copy()
        to_complete[['valid_dem_perc','zmin_m','zmax_m','zmed_m','zmean_m','terminus_lon','terminus_lat','slope_deg','aspect_deg','aspect_sec']] = np.nan
        to_complete[['dem_source']] = ''
        to_complete[['valid_dem_perc']] = 0
        out_df = pd.concat([out_df, to_complete]).sort_index()
        out_df.to_csv(odir + f'/hypsometry_{rgi_reg}_best.csv')
        chosen_dem.append(out_df['dem_source'])

01: After COPDEM, 0 left bad.
01:    DONE.
02: After COPDEM, 0 left bad.
02:    DONE.
03: After COPDEM, 11 left bad.
03: DEM3 and minrange 5 can take over for 1
03: After DEM3 and minrange 5, 10 left bad.
03: ASTER and minrange 5 can take over for 1
03: After ASTER and minrange 5, 9 left bad.
03: TANDEM and minrange 5 can take over for 6
03: After TANDEM and minrange 5, 3 left bad.
03: MAPZEN and minrange 5 can take over for 1
03: After MAPZEN and minrange 5, 2 left bad.
04: After COPDEM, 1 left bad.
04: ASTER and minrange 5 can take over for 1
04: After ASTER and minrange 5, 0 left bad.
04:    DONE.
05: After COPDEM, 4 left bad.
05: DEM3 and minrange 5 can take over for 3
05: After DEM3 and minrange 5, 1 left bad.
05: TANDEM and minrange 5 can take over for 1
05: After TANDEM and minrange 5, 0 left bad.
05:    DONE.
06: After COPDEM, 0 left bad.
06:    DONE.
07: After COPDEM, 0 left bad.
07:    DONE.
08: After COPDEM, 0 left bad.
08:    DONE.
09: After COPDEM, 0 left bad.
09:    DONE.

In [12]:
chosen_dem = pd.concat(chosen_dem)

In [13]:
assert len(chosen_dem) == len(rgi_reg_df_all)

In [14]:
dem_dict = chosen_dem.to_dict()

In [15]:
import json
with open('chosen_dem_RGI62_20251029.json', 'w') as f:
    json.dump(dem_dict, f)

In [16]:
chosen_dem.unique()

array(['COPDEM30', 'COPDEM90', 'TANDEM', 'ASTER', '', 'DEM3', 'MAPZEN',
       'NASADEM', 'RAMP'], dtype=object)

In [18]:
chosen_dem.to_csv('chosen_dem_RGI62_20251029.csv')

In [48]:
chosen_dem

RGI60-01.00001    COPDEM30
RGI60-01.00002    COPDEM30
RGI60-01.00003    COPDEM30
RGI60-01.00004    COPDEM30
RGI60-01.00005    COPDEM30
                    ...   
RGI60-19.02748    COPDEM30
RGI60-19.02749    COPDEM30
RGI60-19.02750    COPDEM30
RGI60-19.02751      TANDEM
RGI60-19.02752    COPDEM30
Name: dem_source, Length: 215547, dtype: object

In [25]:
len(out_df), len(still_no_good), len(out_df), len(rgi_reg_df)

(2752, 130, 2752, 2752)

In [26]:
out_df

area_km2  area_grid_km2  valid_dem_perc  grid_dx      zmin_m  \
RGI60-19.00001    64.608      64.555443             1.0    123.0   -3.395181   
RGI60-19.00002    12.106      12.124323             1.0     59.0   42.001780   
RGI60-19.00003    13.364      13.373274             1.0     61.0   20.524860   
RGI60-19.00004     0.020       0.020304             1.0     12.0  430.968840   
RGI60-19.00005    21.853      21.813750             1.0     75.0   53.507040   
...                  ...            ...             ...      ...         ...   
RGI60-19.02748     0.042       0.042588             1.0     13.0  281.937000   
RGI60-19.02749     0.567       0.567126             1.0     21.0  331.238950   
RGI60-19.02750     4.118       4.122620             1.0     38.0   -0.593543   
RGI60-19.02751     0.011       0.011253             1.0     11.0    1.183587   
RGI60-19.02752     0.528       0.528400             1.0     20.0  982.299000   

                    zmax_m       zmed_m      zmean_m  terminus_lon  \
RGI60-19.00001  1372.20980   339.647280   382.444200    -67.585143   
RGI60-19.00002   773.57916    93.986680   152.451690    -64.720397   
RGI60-19.00003   694.87415   104.124890   175.078260    -64.919990   
RGI60-19.00004   557.55290   484.871950   487.515750    -64.876700   
RGI60-19.00005   568.79944   105.835390   137.178670    -64.950856   
...                    ...          ...          ...           ...   
RGI60-19.02748   538.05650   386.758300   388.785500    -37.731415   
RGI60-19.02749   897.69090   500.441960   514.304600    -36.142659   
RGI60-19.02750  1114.76500   567.628600   516.312700    -37.294666   
RGI60-19.02751    29.76264    23.700293    21.709957    -90.425737   
RGI60-19.02752  1158.52310  1048.031700  1055.859100     37.711228   

                terminus_lat  ...  6325  6375  6425 6475  6525  6575  6625  \
RGI60-19.00001    -66.888134  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
RGI60-19.00002    -67.682130  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
RGI60-19.00003    -67.674090  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
RGI60-19.00004    -67.634951  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
RGI60-19.00005    -67.599785  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
...                      ...  ...   ...   ...   ...  ...   ...   ...   ...   
RGI60-19.02748    -53.984602  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
RGI60-19.02749    -54.836053  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
RGI60-19.02750    -54.174701  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
RGI60-19.02751    -68.864764  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   
RGI60-19.02752    -46.892509  ...   NaN   NaN   NaN  NaN   NaN   NaN   NaN   

                6675  6725  6775  
RGI60-19.00001   NaN   NaN   NaN  
RGI60-19.00002   NaN   NaN   NaN  
RGI60-19.00003   NaN   NaN   NaN  
RGI60-19.00004   NaN   NaN   NaN  
RGI60-19.00005   NaN   NaN   NaN  
...              ...   ...   ...  
RGI60-19.02748   NaN   NaN   NaN  
RGI60-19.02749   NaN   NaN   NaN  
RGI60-19.02750   NaN   NaN   NaN  
RGI60-19.02751   NaN   NaN   NaN  
RGI60-19.02752   NaN   NaN   NaN  

[2752 rows x 152 columns]

area_km2  area_grid_km2  valid_dem_perc  grid_dx  zmin_m  \
RGIId                                                                      
RGI60-19.00444     0.020       0.019584               0     12.0     NaN   
RGI60-19.00513     0.135       0.134325               0     15.0     NaN   
RGI60-19.00537     0.013       0.012816               0     12.0     NaN   
RGI60-19.00579     0.014       0.013968               0     12.0     NaN   
RGI60-19.00735       NaN            NaN               0      NaN     NaN   
...                  ...            ...             ...      ...     ...   
RGI60-19.01522     0.067       0.067032               0     14.0     NaN   
RGI60-19.01790     0.142       0.143100               0     15.0     NaN   
RGI60-19.01807       NaN            NaN               0      NaN     NaN   
RGI60-19.01819       NaN            NaN               0      NaN     NaN   
RGI60-19.01897     0.064       0.063896               0     14.0     NaN   

                zmax_m  zmed_m  zmean_m  terminus_lon  terminus_lat  \
RGIId                                                                 
RGI60-19.00444     NaN     NaN      NaN           NaN           NaN   
RGI60-19.00513     NaN     NaN      NaN           NaN           NaN   
RGI60-19.00537     NaN     NaN      NaN           NaN           NaN   
RGI60-19.00579     NaN     NaN      NaN           NaN           NaN   
RGI60-19.00735     NaN     NaN      NaN           NaN           NaN   
...                ...     ...      ...           ...           ...   
RGI60-19.01522     NaN     NaN      NaN           NaN           NaN   
RGI60-19.01790     NaN     NaN      NaN           NaN           NaN   
RGI60-19.01807     NaN     NaN      NaN           NaN           NaN   
RGI60-19.01819     NaN     NaN      NaN           NaN           NaN   
RGI60-19.01897     NaN     NaN      NaN           NaN           NaN   

                slope_deg  aspect_deg  aspect_sec dem_source  
RGIId                                                         
RGI60-19.00444        NaN         NaN         NaN             
RGI60-19.00513        NaN         NaN         NaN             
RGI60-19.00537        NaN         NaN         NaN             
RGI60-19.00579        NaN         NaN         NaN             
RGI60-19.00735        NaN         NaN         NaN             
...                   ...         ...         ...        ...  
RGI60-19.01522        NaN         NaN         NaN             
RGI60-19.01790        NaN         NaN         NaN             
RGI60-19.01807        NaN         NaN         NaN             
RGI60-19.01819        NaN         NaN         NaN             
RGI60-19.01897        NaN         NaN         NaN             

[130 rows x 14 columns]

In [13]:
output_stats

In [14]:
still_no_good.to_file('still_no_good_rgi19.geojson', driver='GeoJSON')

In [15]:
still_no_good[['area_km2']].rename({'':'area_km2'})

In [13]:
import fiona
fiona.supported_drivers

{'DXF': 'rw',
 'CSV': 'raw',
 'OpenFileGDB': 'r',
 'ESRIJSON': 'r',
 'ESRI Shapefile': 'raw',
 'FlatGeobuf': 'rw',
 'GeoJSON': 'raw',
 'GeoJSONSeq': 'rw',
 'GPKG': 'raw',
 'GML': 'rw',
 'OGR_GMT': 'rw',
 'GPX': 'rw',
 'Idrisi': 'r',
 'MapInfo File': 'raw',
 'DGN': 'raw',
 'PCIDSK': 'raw',
 'OGR_PDS': 'r',
 'S57': 'r',
 'SQLite': 'raw',
 'TopoJSON': 'r'}

In [ ]:
# Continue with other range
min_range = 1
for source in ['NASADEM', 'RAMP', 'DEM3', 'ASTER', 'TANDEM']:
    print(f'Still no good: {len(still_no_good)}')
    
    fp = f'output_vardx/hypsometry_rgi{reg}_{source}.csv'
    hdf = pd.read_csv(fp, index_col=0)
    if 'valid_dem_perc' not in hdf:
        continue
        
    ids = np.where(hdf.columns.values == 'dem_source')[0][0]
    attr_cols = list(hdf.columns[0:ids+1])
    hypso_cols = list(hdf.columns[ids+1:])
        
    hdf = hdf.loc[still_no_good.index]

    ids = np.where(hdf.columns.values == 'dem_source')[0][0]
    attr_cols = list(hdf.columns[0:ids+1])
    hypso_cols = list(hdf.columns[ids+1:])

    hdf_stats = hdf[attr_cols].copy()
    hdf_hypso = hdf[hypso_cols]
    
    valid = (~ hdf_stats.index.isin(output_stats.index)) & (hdf_stats.valid_dem_perc > 0.99) 
    valid = valid & (hdf_stats.zmin_m > -99) & ((hdf_stats.zmax_m - hdf_stats.zmin_m) > min_range)
    if len(hdf_stats.loc[valid].copy()) == 0:
        continue
    print(f'{source} can take over for {len(hdf_stats.loc[valid].copy())}')
    output_stats = pd.concat([output_stats, hdf_stats.loc[valid].copy()]).sort_index()
    output_hypso = pd.concat([output_hypso, hdf_hypso.loc[valid].copy()]).sort_index()
    still_no_good = rgi_reg_df.loc[~ rgi_reg_df.index.isin(output_stats.index)]
    if len(still_no_good) == 0:
        break

In [ ]:
still_no_good.anlys_id.values

In [ ]:
import shapely.geometry as shpg
geoms = [shpg.Point(x, y) for x, y in zip(output_stats.terminus_lon, output_stats.terminus_lat)]

In [ ]:
output_stats['geometry'] = geoms

In [ ]:
odf = gpd.GeoDataFrame(output_stats)

In [ ]:
odf.crs = 'EPSG:4326'

In [ ]:
odf.to_file('term_points_rgi01.shp')

In [ ]:
[len(c) for c in odf.columns]

In [ ]:
odf.columns

In [ ]:
odf

In [ ]:
output_stats.index

In [ ]:
rgi_reg_df.index

In [ ]:
still_no_good

In [ ]:
NASADEM -> GIMP -> RAMP -> DEM3 -> ASTER -> TANDEM 

In [ ]:
df_hypso = []
for fp in glob.glob(f'output_vardx/hypsometry_rgi{reg}_*.csv'):
    tmp = pd.read_csv(fp, index_col=0)
    if 'valid_dem_perc' not in tmp:
        continue
    df_hypso.append(tmp)
df_hypso = pd.concat(df_hypso)

In [ ]:
ids = np.where(df_hypso.columns.values == 'dem_source')[0][0]
attr_cols = df_hypso.columns[0:ids+1]
hypso_cols = ['dem_source'] + list(df_hypso.columns[ids+1:])
# attr_cols, hypso_cols

In [ ]:
df_hypso_stats = df_hypso[attr_cols].copy()
df_hypso = df_hypso[hypso_cols]

In [ ]:
reg_hypso = pd.DataFrame()
for source in df_hypso.dem_source.unique():
    tt = df_hypso.loc[df_hypso.dem_source == source].drop('dem_source', axis=1).T
    tt.index = tt.index.astype(int)
    tt = tt.sort_index()
    reg_hypso[source] = tt.loc[-25:].sum(axis=1)

In [ ]:
reg_hypso

In [ ]:
df_hypso[['dem_source', '5975']].dropna()

In [ ]:
df_hypso[['dem_source', '-75']].dropna().dem_source.unique()

In [ ]:
df_hypso[['dem_source', '-25']].dropna().dem_source.unique()

In [ ]:
df_hypso[['dem_source', '-25']].dropna()

In [ ]:
reg_hypso[['ALASKA', 'COPDEM30', 'COPDEM90', 'ASTER']].plot();

In [ ]:
(reg_hypso['COPDEM30'] -  reg_hypso['COPDEM90']).plot();

In [ ]:
pick = df_hypso.loc['RGI2000-v7.0-G-01-06486'].set_index('dem_source', drop=True).T
pick.index = pick.index.astype(int)
pick = pick.sort_index().loc[-25:]
pick.plot();

In [ ]:
df_hypso_stats

In [ ]:
reg_hypso

In [ ]:
df_stats.COPDEM30.unique()

In [ ]:
df.loc[df.COPDEM30.isnull()]

In [ ]:
baaad = df.loc[df.COPDEM30.isnull() & df.COPDEM90.isnull()]

In [ ]:
baaad

In [ ]:
len(baaad)

In [ ]:
baaad.sum()

NASADEM -> GIMP -> RAMP -> DEM3 -> ASTER -> TANDEM 

In [ ]:
len(baaad.loc[(baaad.RAMP != 1)])

In [ ]:
len(baaad.loc[(baaad.RAMP != 1) & (baaad.DEM3 != 1)])

In [ ]:
len(baaad.loc[(baaad.RAMP != 1) & (baaad.DEM3 != 1) & (baaad.ASTER != 1)])

In [ ]:
len(baaad.loc[(baaad.RAMP != 1) & (baaad.DEM3 != 1) & (baaad.ASTER != 1) & (baaad.TANDEM != 1)])

In [ ]:
baaad.loc[(baaad.RAMP != 1) & (baaad.DEM3 != 1) & (baaad.ASTER != 1) & (baaad.TANDEM != 1)]

In [ ]:
rgi_reg_df.loc[rgi_reg_df.rgi_id == 'RGI2000-v7.0-G-19-02348']

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
x = np.linspace(0.01, 100, 1000)
plt.plot(x, np.clip(14. * np.sqrt(x) + 10, None, 100));
plt.plot(x, np.clip(8. * np.sqrt(x) + 10, None, 100));

In [ ]:
rgi_reg_df.loc[rgi_reg_df.o1region == '11'].area_km2.max()

In [ ]:
y = d1 * sqrt(a) + d2

In [ ]:
d1 = 14
d2 = 10
y = 50
((y - d2)/d1)**2

In [ ]:
y = 100
((y - d2)/d1)**2

In [ ]:
import pandas as pd

In [ ]:
x = [0.01, 1, 2, 3, 4, 5, 10, 20, 30, 40] + list(range(41, 200))

In [ ]:
tdf = pd.DataFrame(index=x)

In [ ]:
tdf['dx'] = np.clip(d1 * np.sqrt(x) + d2, None, 100)

In [ ]:
tdf['npix'] = tdf.index * 1e6 / tdf['dx']**2

In [ ]:
tdf['npix'].plot();

In [ ]:
import numpy as np
from shapely.geometry import Point, LineString, LinearRing
from shapely.geometry.polygon import Polygon
from geopandas import GeoSeries
import matplotlib.pyplot as plt

x_data = np.array([1, 1, 1.5, 2, 2, 3]) 
y_data = np.array([1, 2, 2, 2, 2.5, 3])
p = [2, 1, 0, 3, 4, 5]

plt.plot(x_data, y_data, 'o');

In [ ]:
LineString(coordinates=np.asarray((x_data, y_data)).T).length

In [ ]:
LineString(coordinates=np.asarray((x_data[p], y_data[p])).T).length

In [ ]:
LinearRing(coordinates=np.asarray((x_data[p], y_data[p])).T)

In [ ]:
np.argmin([1, 1, 2, 3])